In [1]:
import pandas as pd
import json
import plotly.graph_objects as go

In [2]:
df_Bev = pd.read_csv('Bevölkerung_modified.csv')
df_Bev.head()

Unnamed: 0   Kreise  Count  id_Kreis
0           0  Kreis 1    239         1
1           1  Kreis 2    180         2
2           2  Kreis 3    180         3
3           3  Kreis 4    180         4
4           4  Kreis 5    120         5

In [3]:
df_migros = pd.read_csv('M_modified.csv')
df_migros.head()

Unnamed: 0.1  Unnamed: 0  \
0             0           0   
1             1           1   
2             2           2   
3             3           3   
4             4           4   

                                             address               name  \
0       Badenerstrasse 376, 8004 Zürich, Switzerland  Migros Supermarkt   
1  Birmensdorferstrasse 140, 8003 Zürich, Switzer...  Migros Supermarkt   
2  Birmensdorferstrasse 320, 8055 Zürich, Switzer...  Migros Supermarkt   
3           Etzelstrasse 3, 8038 Zürich, Switzerland  Migros Supermarkt   
4    Falkenstrasse 19 - 21, 8008 Zürich, Switzerland             Migros   

   rating  nr_users_rating        lat       lng  Kreis_id  
0     4.1              463  47.379105  8.508754         4  
1     4.2              636  47.370066  8.520107         3  
2     4.3              520  47.369956  8.508721         3  
3     4.3              616  47.344706  8.529962         2  
4     4.2              419  47.365446  8.547967         1

In [4]:
df_competitors = pd.read_csv('modified.csv')
df_competitors.head()

Unnamed: 0.1  Unnamed: 0  \
0             0           0   
1             1           1   
2             2           2   
3             3           3   
4             4           4   

                                             address  \
0         Am Suteracher 14, 8048 Zürich, Switzerland   
1       Badenerstrasse 244, 8004 Zürich, Switzerland   
2       Badenerstrasse 333, 8003 Zürich, Switzerland   
3          Bahnhofbrücke 1, 8001 Zürich, Switzerland   
4  Birmensdorferstrasse 200, 8003 Zürich, Switzer...   

                                      name  rating  users_rating_num  \
0        Coop Supermarkt Zürich Suteracher     4.1               137   
1         Coop Supermarkt Zürich Lochergut     4.2               662   
2  Coop Supermarkt Zürich Albisriederplatz     4.1               749   
3     Coop Supermarkt Zürich Bahnhofbrücke     4.3              3000   
4          Coop Supermarkt Zürich Wiedikon     4.3               646   

         lat       lng name_s  Kreis_id  
0  47.389955  8.472095   Coop         9  
1  47.375734  8.517334   Coop         4  
2  47.377711  8.511107   Coop         3  
3  47.376458  8.542357   Coop         1  
4  47.370796  8.516052   Coop         3

In [5]:
list_stores_names = df_competitors.name_s.unique().tolist()
list_stores_names

['Coop', 'Denner', 'Aldi', 'Lidl', 'Spar']

In [6]:
with open('stadtkreise.json') as json_file:
    stadtkreise_ = json.load(json_file)

def set_ID(kreis):
    for i in range(len(kreis['features'])):
        kreis['features'][i]['id'] = kreis['features'][i]['properties']['name']
    return kreis

stadtkreise_ = set_ID(stadtkreise_)

In [7]:
# from here on
df_migros.head()

Unnamed: 0.1  Unnamed: 0  \
0             0           0   
1             1           1   
2             2           2   
3             3           3   
4             4           4   

                                             address               name  \
0       Badenerstrasse 376, 8004 Zürich, Switzerland  Migros Supermarkt   
1  Birmensdorferstrasse 140, 8003 Zürich, Switzer...  Migros Supermarkt   
2  Birmensdorferstrasse 320, 8055 Zürich, Switzer...  Migros Supermarkt   
3           Etzelstrasse 3, 8038 Zürich, Switzerland  Migros Supermarkt   
4    Falkenstrasse 19 - 21, 8008 Zürich, Switzerland             Migros   

   rating  nr_users_rating        lat       lng  Kreis_id  
0     4.1              463  47.379105  8.508754         4  
1     4.2              636  47.370066  8.520107         3  
2     4.3              520  47.369956  8.508721         3  
3     4.3              616  47.344706  8.529962         2  
4     4.2              419  47.365446  8.547967         1

In [25]:
fig = go.Figure(go.Choroplethmapbox(geojson=stadtkreise_, locations=df_Bev.id_Kreis, z=df_Bev.Count,
                                    colorscale="Viridis",
                                    marker_opacity=0.5, 
                                    marker_line_width=0,
                                    text = df_Bev['id_Kreis'],
                                    hovertemplate = "Kreis %{text}<extra></extra>",
                                    ))

#spot=1.3
fig.add_scattermapbox(lat = df_migros.lat.tolist(),
                      lon = df_migros.lng.tolist(),
                      line_color = 'red',
                      mode="markers+text",
                      marker=go.scattermapbox.Marker(size= np.log(df_migros.nr_users_rating)*1.5),
                      text=df_migros["address"],
                      customdata=df_migros[['rating', 'nr_users_rating', 'Kreis_id']],
                      hovertemplate = "MIGROS <br>%{text}<br>Kreis %{customdata[2]} <br>Lat: %{lat:.2f}   Lon: %{lon:.2f}<br>Rating: %{customdata[0]},  Nr Ratings: %{customdata[1]}<extra></extra>")

df_coop = df_competitors[df_competitors.name_s == 'Coop']
fig.add_scattermapbox(lat = df_coop.lat.tolist(),
                      lon = df_coop.lng.tolist(),
                      line_color = 'green',
                      mode="markers+text",
                      marker=go.scattermapbox.Marker(size= np.log(df_coop.users_rating_num)*1.5), 
                      # marker=go.scattermapbox.Marker( size= 50*df_coop.users_rating_num/rating_num_max),
                      text=df_coop["address"],
                      customdata=df_coop[['rating', 'users_rating_num', 'Kreis_id']],
                      hovertemplate = "COOP <br>%{text}<br>Kreis %{customdata[2]} <br>Lat: %{lat:.2f}   Lon: %{lon:.2f}<br>Rating: %{customdata[0]},  Nr Ratings: %{customdata[1]}<extra></extra>")

list_stores_names = ['Denner', 'Aldi', 'Lidl', 'Spar']
for store in list_stores_names:
    df_aux = df_competitors[df_competitors.name_s == store]
    fig.add_scattermapbox(lat = df_aux.lat.tolist(),
                        lon = df_aux.lng.tolist(),
                        line_color = 'blue',
                        mode="markers+text",
                        marker=go.scattermapbox.Marker(size= np.log(df_aux.users_rating_num)*1.5),
                        #marker={"size": 7},
                        text=df_aux["address"],
                        customdata=df_aux[['rating', 'users_rating_num', 'Kreis_id', 'name_s']],
                        hovertemplate = "%{customdata[3]} <br>%{text}<br>Kreis %{customdata[2]} <br>lat: %{lat:.2f}   lon: %{lon:.2f}<br>Rating: %{customdata[0]},  Nr Ratings: %{customdata[1]}<extra></extra>",)


fig.update_layout(mapbox_style="carto-positron",
                  mapbox_zoom=10, mapbox_center = {"lat": 47.4, "lon": 8.6})
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

In [ ]:
fig = go.Figure(go.Choroplethmapbox(geojson=stadtkreise_, locations=df_Bev.id_Kreis, z=df_Bev.Count,
                                    colorscale="Viridis",
                                    marker_opacity=0.5, 
                                    marker_line_width=0,
                                    text = df_Bev['id_Kreis'],
                                    hovertemplate = "Kreis %{text}<extra></extra>",
                                    ))

fig.add_scattermapbox(lat = df_migros.lat.tolist(),
                      lon = df_migros.lng.tolist(),
                      line_color = 'red',
                      mode="markers+text",
                      marker={"size": 7},
                      text=df_migros["address"],
                      customdata=df_migros[['rating', 'nr_users_rating', 'Kreis_id']],
                      hovertemplate = "MIGROS <br>%{text}<br>Kreis %{customdata[2]} <br>Lat: %{lat:.2f}   Lon: %{lon:.2f}<br>Rating: %{customdata[0]},  Nr Ratings: %{customdata[1]}<extra></extra>")

df_coop = df_competitors[df_competitors.name_s == 'Coop']
fig.add_scattermapbox(lat = df_coop.lat.tolist(),
                      lon = df_coop.lng.tolist(),
                      line_color = 'green',
                      mode="markers+text",
                      marker={"size": 7},
                      text=df_coop["address"],
                      customdata=df_coop[['rating', 'users_rating_num', 'Kreis_id']],
                      hovertemplate = "COOP <br>%{text}<br>Kreis %{customdata[2]} <br>Lat: %{lat:.2f}   Lon: %{lon:.2f}<br>Rating: %{customdata[0]},  Nr Ratings: %{customdata[1]}<extra></extra>")

list_stores_names = ['Denner', 'Aldi', 'Lidl', 'Spar']

for store in list_stores_names:
    df_aux = df_competitors[df_competitors.name_s == store]
    fig.add_scattermapbox(lat = df_aux.lat.tolist(),
                        lon = df_aux.lng.tolist(),
                        line_color = 'blue',
                        mode="markers+text",
                        marker={"size": 7},
                        text=df_aux["address"],
                        customdata=df_aux[['rating', 'users_rating_num', 'Kreis_id', 'name_s']],
                        hovertemplate = "%{customdata[3]} <br>%{text}<br>Kreis %{customdata[2]} <br>lat: %{lat:.2f}   lon: %{lon:.2f}<br>Rating: %{customdata[0]},  Nr Ratings: %{customdata[1]}<extra></extra>",)


fig.update_layout(mapbox_style="carto-positron",
                  mapbox_zoom=10, mapbox_center = {"lat": 47.4, "lon": 8.6})
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

---
## Count Location of all stores:

In [ ]:
df_count = pd.DataFrame()
df_count['Kreis_id'] = [id for id in range(1, 13)]

count = []
for id in range(1, 13):
    count.append(len(df_migros[df_migros['Kreis_id'] == id]) + len(df_competitors[df_competitors['Kreis_id'] == id]))
    
df_count['Count'] = count

In [ ]:
fig = go.Figure(go.Choroplethmapbox(geojson=stadtkreise_, locations=df_count.Kreis_id, z=df_count.Count,
                                    colorscale="Viridis",
                                    marker_opacity=0.5, 
                                    marker_line_width=0,
                                    ))

fig.update_layout(mapbox_style="carto-positron",
                  mapbox_zoom=10, mapbox_center = {"lat": 47.4, "lon": 8.6})
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

---
## Locations Migros:

In [ ]:
df_count = pd.DataFrame()
df_count['Kreis_id'] = [id for id in range(1, 13)]

count = []
for id in range(1, 13):
    count.append(len(df_migros[df_migros['Kreis_id'] == id]))
    
df_count['Count'] = count

In [ ]:
fig = go.Figure(go.Choroplethmapbox(geojson=stadtkreise_, locations=df_count.Kreis_id, z=df_count.Count,
                                    colorscale="Viridis",
                                    marker_opacity=0.5, 
                                    marker_line_width=0,
                                    ))

fig.update_layout(mapbox_style="carto-positron",
                  mapbox_zoom=10, mapbox_center = {"lat": 47.4, "lon": 8.6})
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

---
# Locations other stores:

In [ ]:
df_count = pd.DataFrame()
df_count['Kreis_id'] = [id for id in range(1, 13)]

count = []
for id in range(1, 13):
    count.append(len(df_competitors[df_competitors['Kreis_id'] == id]))
    
df_count['Count'] = count

In [ ]:
fig = go.Figure(go.Choroplethmapbox(geojson=stadtkreise_, locations=df_count.Kreis_id, z=df_count.Count,
                                    colorscale="Viridis",
                                    marker_opacity=0.5, 
                                    marker_line_width=0,
                                    ))

fig.update_layout(mapbox_style="carto-positron",
                  mapbox_zoom=10, mapbox_center = {"lat": 47.4, "lon": 8.6})
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

---
## Distance:

In [ ]:
from math import radians, cos, sin, asin, sqrt

In [ ]:
def distance(coords_1, coords_2):
    # Unpack tuples:
    lat1, lon1 = coords_1
    lat2, lon2 = coords_2

    # The math module contains a function named
    # radians which converts from degrees to radians.
    lon1 = radians(lon1)
    lon2 = radians(lon2)
    lat1 = radians(lat1)
    lat2 = radians(lat2)
      
    # Haversine formula
    dlon = lon2 - lon1
    dlat = lat2 - lat1
    a = sin(dlat / 2)**2 + cos(lat1) * cos(lat2) * sin(dlon / 2)**2
 
    c = 2 * asin(sqrt(a))
    
    # Radius of earth in kilometers. Use 3956 for miles
    r = 6371
      
    # calculate the result
    return(c * r) # => Distance in Kilometers

In [ ]:
dict_dist = dict()

for id in range(1, 13):
    """
    Debug:
    display(df_migros[df_migros['Kreis_id'] == id])
    display(df_competitors[df_competitors['Kreis_id'] == id])
    print('--------------------------------------------------------------------------')
    """
    lat_m = df_migros[df_migros['Kreis_id'] == id]['lat'].tolist()
    lon_m = df_migros[df_migros['Kreis_id'] == id]['lng'].tolist()
    coords_m = list(zip(lat_m, lon_m))
    # print(coords_m)
    
    distances = []
    for coord_m in coords_m:
        lat_c = df_competitors[df_competitors['Kreis_id'] == id]['lat'].tolist()
        lon_c = df_competitors[df_competitors['Kreis_id'] == id]['lng'].tolist()
        coords_c = list(zip(lat_c, lon_c))
        
        for coord_c in coords_c:
            distances.append(distance(coord_m, coord_c))
    dict_dist[id] = distances

dict_dist

{1: [1.2953246849374662,
  1.549611599346076,
  0.12742600768474355,
  0.9605847526928063,
  1.5496208931903295,
  1.13083297602406,
  1.343977397959881,
  1.204653683993906,
  0.625417030433934,
  0.24679847711702887,
  0.08263493986727002,
  1.3674247244199769,
  0.8280460890573024,
  0.08262328613879173,
  0.5204714702734722,
  0.5936804299615526,
  0.4419804037385513,
  0.9581596735044765,
  0.48760011864718705,
  0.3239118316879321,
  1.3185174086739824,
  0.5834936471308655,
  0.3239428642433428,
  0.30067993463537496,
  0.25414114269530463,
  0.218965862364419,
  0.8197000491748972,
  0.23213761473183142,
  0.12966818104998337,
  1.3868096271505093,
  0.8861201226457464,
  0.12964331072978386,
  0.5806295623496244,
  0.6643095555043227,
  0.50496032174957,
  0.9982153314502765,
  0.4851516153295563,
  0.33166904868881203,
  1.304770015899488,
  0.569630905733347,
  0.331699820489749,
  0.28627758973912876,
  0.24573126354271757,
  0.2047063677071567,
  0.8053550844733949],
 2: [

In [ ]:
# Get minimal-distance:
dict_min_dist = dict()

for id, distances in dict_dist.items():
    dict_min_dist[id] = min(distances)

dict_min_dist

{1: 0.08262328613879173,
 2: 0.03375381654016506,
 3: 0.013287436505246424,
 4: 0.030112193126122306,
 5: 0.05402131474973987,
 6: 0.24133673113074697,
 7: 0.029251046853322107,
 8: 0.05782669776890796,
 9: 0.042188174986880385,
 10: 0.026173965060887122,
 11: 0.014408922368267636,
 12: 0.13111053031515846}

In [ ]:
df_dist = pd.DataFrame(dict_min_dist.items(), columns=['Kreis_id', 'Distance'])
df_dist

Kreis_id  Distance
0          1  0.082623
1          2  0.033754
2          3  0.013287
3          4  0.030112
4          5  0.054021
5          6  0.241337
6          7  0.029251
7          8  0.057827
8          9  0.042188
9         10  0.026174
10        11  0.014409
11        12  0.131111

In [ ]:
fig = go.Figure(go.Choroplethmapbox(geojson=stadtkreise_, locations=df_dist.Kreis_id, z=df_dist.Distance,
                                    colorscale="Viridis",
                                    marker_opacity=0.5, 
                                    marker_line_width=0,
                                    ))

fig.update_layout(mapbox_style="carto-positron",
                  mapbox_zoom=10, mapbox_center = {"lat": 47.4, "lon": 8.6})
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()